In [15]:
from py2neo import Graph
from bs4 import BeautifulSoup
import pywikibot
import pandas as pd
import requests
from sklearn.feature_extraction.text import TfidfVectorizer
import wikipedia
import spacy
import os
nlp = spacy.load("en_core_web_sm")
import gensim
from collections import defaultdict
from time import sleep
from gensim.parsing.preprocessing import strip_multiple_whitespaces, preprocess_string, remove_stopwords, strip_tags, strip_punctuation 
import pickle
from time import time

In [2]:
#verify if category actually exists on online Wikipedia
def categoryExist(name):
    res = requests.get("https://en.wikipedia.org/wiki/Category:" + name)
    soup = BeautifulSoup(res.content, "html.parser")
    div = soup.find("div", {"id": "mw-normal-catlinks"})
    if(div):
        return True
    else:
        return False

#Use beautifulsoup to scrape the bottom categories of a parent category (these we don't want)
def getBadCategories(parent):
    res = requests.get("https://en.wikipedia.org/wiki/Category:" + parent)
    soup = BeautifulSoup(res.content, "html.parser")
    div = soup.find("div", {"id": "mw-normal-catlinks"})
    if(div):
        to_return = []
        for item in div.findAll("li"):
            to_return.append("_".join(item.get_text().split(" ")))
        return to_return
    else:
        #parent does not exist
        return []

def getSubCategories(name):
    site = pywikibot.Site()
    gen = pywikibot.Category(site,'Category:' + name).subcategories(recurse=False)
    subcats = []
    for item in gen:
        subcats.append("_".join(item.aslink().split(":")[1][:-2].split(" ")))
    return subcats  

In [3]:
blacklist = ["July_events"] #nodes that should not be visited
all_nodes = []
all_relations = [] #child parent
visited = []
def buildGraph(root, path):
    path = path + "/" + root
    print("Current Path: " + path)
    print()
    if((not categoryExist(root)) or (root in blacklist)):
        print("Category DNE or is BLACKLISTED")
        print()
        return
    if(root in visited):
        print("VISITED ALREADY")
        print()
        return
    
    visited.append(root)
    
    #add the node
    all_nodes.append(root)
    
    #get all subcategories
    sub_cat = getSubCategories(root)
    if(len(sub_cat) == 0): #base case
        return

    
    #add all the relationships
    for item in sub_cat:
        #check if this relationship already exists (cycle)
        relation = item + " " + root
        if(relation in all_relations):
            print("Relation already exists: ", relation)
            print()
            return
        all_relations.append(item + " " + root)
   
    #recurse on all sub nodes
    for item in sub_cat:
        buildGraph(item, path)


In [4]:
category = "Calculus"

In [4]:

buildGraph(category, "")

Current Path: /Calculus

Current Path: /Calculus/Differential_calculus

Current Path: /Calculus/Differential_calculus/Differentiation_rules

Current Path: /Calculus/Differential_calculus/Differential_equations

Current Path: /Calculus/Differential_calculus/Differential_equations/Bifurcation_theory

Current Path: /Calculus/Differential_calculus/Differential_equations/Boundary_value_problems

Current Path: /Calculus/Differential_calculus/Differential_equations/Boundary_value_problems/Boundary_conditions

Current Path: /Calculus/Differential_calculus/Differential_equations/Calculus_of_variations

Current Path: /Calculus/Differential_calculus/Differential_equations/Calculus_of_variations/Action_(physics)

Current Path: /Calculus/Differential_calculus/Differential_equations/Calculus_of_variations/Action_(physics)/Cell_movement

Current Path: /Calculus/Differential_calculus/Differential_equations/Calculus_of_variations/Action_(physics)/Cell_movement/Motor_proteins

Current Path: /Calculus/Di

Current Path: /Calculus/Differential_calculus/Differential_equations/Partial_differential_equations/Exactly_solvable_models/Integrable_systems/Quantum_models

Current Path: /Calculus/Differential_calculus/Differential_equations/Partial_differential_equations/Exactly_solvable_models/Solitons

Current Path: /Calculus/Differential_calculus/Differential_equations/Partial_differential_equations/Hyperbolic_partial_differential_equations

Current Path: /Calculus/Differential_calculus/Differential_equations/Partial_differential_equations/Integrable_systems

VISITED ALREADY

Current Path: /Calculus/Differential_calculus/Differential_equations/Partial_differential_equations/Maxwell's_equations

Current Path: /Calculus/Differential_calculus/Differential_equations/Partial_differential_equations/Nonlinear_partial_differential_equations

Current Path: /Calculus/Differential_calculus/Differential_equations/Partial_differential_equations/Parabolic_partial_differential_equations

Current Path: /Calculu

VISITED ALREADY

Current Path: /Calculus/Mathematical_series/Summability_theory/Divergent_series

VISITED ALREADY

Current Path: /Calculus/Mathematical_series/Summability_theory/Sequence_spaces

Current Path: /Calculus/Mathematical_series/Summability_theory/Summability_methods

VISITED ALREADY

Current Path: /Calculus/Mathematical_series/Summability_theory/Tauberian_theorems

VISITED ALREADY

Current Path: /Calculus/Monadology

Current Path: /Calculus/Multivariable_calculus

Current Path: /Calculus/Multivariable_calculus/Differential_forms

Current Path: /Calculus/Multivariable_calculus/Differential_forms/Hodge_theory

VISITED ALREADY

Current Path: /Calculus/Multivariable_calculus/Differential_operators

VISITED ALREADY

Current Path: /Calculus/Multivariable_calculus/Morse_theory

VISITED ALREADY

Current Path: /Calculus/Multivariable_calculus/Partial_differential_equations

VISITED ALREADY

Current Path: /Calculus/Multivariable_calculus/Potentials

Current Path: /Calculus/Multivariab

In [6]:
len(all_relations)

168

In [5]:
fileName = "data/" + category

In [8]:
#save graph to files
with open(fileName + '_nodes.txt', 'w') as f:
    for item in all_nodes:
        f.write("%s\n" % item)

with open(fileName + '_relations.txt', 'w') as f:
    for item in all_relations:
        f.write("%s\n" % item)        

In [19]:
wikipedia.page("Wave_mechanics")
print(search)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [18]:
def fetch_wiki_pages(fileName, pagesToSearch = None):
    wiki_pages_dir = fileName + "_pages"
    if not os.path.exists(wiki_pages_dir):
        os.makedirs(wiki_pages_dir)
    file = open(fileName + '_nodes.txt', "r")
    articles_cleaned = []
    failures = []
    if(pagesToSearch is None):
        pagesToSearch = file
    for line in pagesToSearch:
        line = line.strip()
        wiki_page_path = wiki_pages_dir + "/" + line + ".txt"
        print(wiki_page_path)
        if(os.path.isfile(wiki_page_path)):
            print(wiki_page_path + " already exists")
            continue
        #sleep(10)
        print("fetching ==" + line + "==")
    #     all_good = True
    #     while(True):
        try:
            search = wikipedia.search(line.rstrip("\n"))[0]
            page = wikipedia.page(search)
        except wikipedia.DisambiguationError as e:
            print("ERROR: Disambiguation error")
            for option in e.options:
                try:
                    page = wikipedia.page(option)
                    print("Scraping " + option + " instead")
                    break;
                except wikipedia.DisambiguationError:
                    continue;
                    
        except wikipedia.WikipediaException as e: # search is too busy
            print("ERROR: search too busy")
            failures.append(line)
            continue
            #all_good = False
        except Exception:
            print("ERROR: random error")
            articles_cleaned.append("")
            failures.append(line)
            continue
    #         if all_good:
    #             break;
        #page = wikipedia.page(wikipedia.search(line.rstrip("\n"))[0])
        content = page.content
        
        text_file = open(wiki_page_path, "w")
        text_file.write(content)
        text_file.close()
        print("finished")
    file.close()
    return failures

def preprocess(x):
    x = gensim.utils.simple_preprocess(x)
    x = " ".join(x)
    
    CUSTOM_FILTERS = [lambda x: x.lower(), strip_tags, strip_punctuation, remove_stopwords]
    x = preprocess_string(x, CUSTOM_FILTERS)
    return x

def clean_wiki_pages(fileName):
    wiki_pages_dir = fileName + "_pages"
    articles_cleaned = []
    file = open(fileName + '_nodes.txt', "r")
    FREQ_THRESHOLD = 3
    for line in file:
        line = line.strip()
        wiki_page_path = wiki_pages_dir + "/" + line + ".txt"
        if(not os.path.isfile(wiki_page_path)):
            print("ERROR: " + wiki_page_path + " does not exist")
            articles_cleaned.append("")
            continue
        
        print("cleaning: " + wiki_page_path)
        f = open(wiki_page_path, "r")
        content = f.read()

        cleaned = preprocess(content) #strip punctuations and stopwords and weird characters
        cleaned = " ".join(cleaned)
        doc = nlp(cleaned)
        lemm = [token.lemma_ for token in doc]
        d = defaultdict(int)
        for item in lemm:
            d[item] += 1
        tokens=[key for key,value in d.items() if value>FREQ_THRESHOLD] #all words with frequency of more than some number
        texts = [word for word in lemm if word in tokens]
        texts = " ".join(texts)
        articles_cleaned.append(texts)
    return articles_cleaned

In [19]:
failures = fetch_wiki_pages(fileName)
print(len(failures))
while(len(failures) > 0):
    failures = fetch_wiki_pages(fileName, failures)

data/Calculus_pages/Calculus.txt
data/Calculus_pages/Calculus.txt already exists
data/Calculus_pages/Differential_calculus.txt
data/Calculus_pages/Differential_calculus.txt already exists
data/Calculus_pages/Differentiation_rules.txt
data/Calculus_pages/Differentiation_rules.txt already exists
data/Calculus_pages/Differential_equations.txt
data/Calculus_pages/Differential_equations.txt already exists
data/Calculus_pages/Bifurcation_theory.txt
data/Calculus_pages/Bifurcation_theory.txt already exists
data/Calculus_pages/Boundary_value_problems.txt
data/Calculus_pages/Boundary_value_problems.txt already exists
data/Calculus_pages/Boundary_conditions.txt
data/Calculus_pages/Boundary_conditions.txt already exists
data/Calculus_pages/Calculus_of_variations.txt
data/Calculus_pages/Calculus_of_variations.txt already exists
data/Calculus_pages/Action_(physics).txt
data/Calculus_pages/Action_(physics).txt already exists
data/Calculus_pages/Cell_movement.txt
data/Calculus_pages/Cell_movement.txt

finished
data/Calculus_pages/Interferometric_telescopes.txt
fetching ==Interferometric_telescopes==
finished
data/Calculus_pages/Interferometric_gravitational-wave_instruments.txt
fetching ==Interferometric_gravitational-wave_instruments==
finished
data/Calculus_pages/Aperture_synthesis.txt
fetching ==Aperture_synthesis==
finished
data/Calculus_pages/Synthetic_aperture_radar.txt
fetching ==Synthetic_aperture_radar==
finished
data/Calculus_pages/Measurement_and_signature_intelligence.txt
fetching ==Measurement_and_signature_intelligence==
finished
data/Calculus_pages/Space_synthetic_aperture_radar.txt
fetching ==Space_synthetic_aperture_radar==
finished
data/Calculus_pages/Synthetic_aperture_radar_satellites.txt
fetching ==Synthetic_aperture_radar_satellites==
finished
data/Calculus_pages/Stability_theory.txt
fetching ==Stability_theory==
finished
data/Calculus_pages/Stochastic_differential_equations.txt
fetching ==Stochastic_differential_equations==
finished
data/Calculus_pages/Margina

In [20]:
articles_cleaned = clean_wiki_pages(fileName)
print(len(articles_cleaned))

cleaning: data/Calculus_pages/Calculus.txt
cleaning: data/Calculus_pages/Differential_calculus.txt
cleaning: data/Calculus_pages/Differentiation_rules.txt
cleaning: data/Calculus_pages/Differential_equations.txt
cleaning: data/Calculus_pages/Bifurcation_theory.txt
cleaning: data/Calculus_pages/Boundary_value_problems.txt
cleaning: data/Calculus_pages/Boundary_conditions.txt
cleaning: data/Calculus_pages/Calculus_of_variations.txt
cleaning: data/Calculus_pages/Action_(physics).txt
cleaning: data/Calculus_pages/Cell_movement.txt
cleaning: data/Calculus_pages/Motor_proteins.txt
cleaning: data/Calculus_pages/Taxes_(biology).txt
cleaning: data/Calculus_pages/Variational_analysis.txt
cleaning: data/Calculus_pages/Variational_analysts.txt
cleaning: data/Calculus_pages/Convex_analysis.txt
cleaning: data/Calculus_pages/Convex_optimization.txt
cleaning: data/Calculus_pages/Generalized_convexity.txt
cleaning: data/Calculus_pages/Generalizations_of_the_derivative.txt
cleaning: data/Calculus_pages/

### Load Features

In [21]:
from gensim.test.utils import common_texts
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
import nltk.data

tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')
tokenizer.tokenize(articles_cleaned[0])

['calculus call infinitesimal calculus calculus infinitesimal mathematical study continuous change way study shape algebra study operation branch differential calculus integral calculus rate change slope curve integral calculus quantity area curve branch relate fundamental theorem calculus use fundamental notion infinite infinite series define limit infinitesimal calculus develop independently th century isaac newton gottfrie wilhelm leibniz today calculus use science mathematic calculus mathematical analysis study function limit word calculus word meaning small meaning medicine calculation word today usually method computation method calculation relate theory calculus calculus calculus calculus process calculus calculus develop th century europe isaac newton gottfrie wilhelm leibniz independently publish time ancient middle later europe ancient ancient introduce idea lead integral calculus develop idea rigorous way calculation volume area integral calculus th method mathematic method 

In [22]:
def read_corpus():
    for i, doc in enumerate(articles_cleaned):
        yield TaggedDocument(doc, [i]) #formerly gensim.utils.simple_preprocess

documents = list(read_corpus())
model = Doc2Vec(vector_size=300, min_count=2, epochs=1) #TODO: increase epoch count

In [23]:
model.build_vocab(documents)

In [24]:
%time model.train(documents, total_examples=model.corpus_count, epochs=model.epochs)

CPU times: user 594 ms, sys: 8.58 ms, total: 602 ms
Wall time: 223 ms


In [25]:
model

In [27]:
articles_cleaned[0]

'calculus call infinitesimal calculus calculus infinitesimal mathematical study continuous change way study shape algebra study operation branch differential calculus integral calculus rate change slope curve integral calculus quantity area curve branch relate fundamental theorem calculus use fundamental notion infinite infinite series define limit infinitesimal calculus develop independently th century isaac newton gottfrie wilhelm leibniz today calculus use science mathematic calculus mathematical analysis study function limit word calculus word meaning small meaning medicine calculation word today usually method computation method calculation relate theory calculus calculus calculus calculus process calculus calculus develop th century europe isaac newton gottfrie wilhelm leibniz independently publish time ancient middle later europe ancient ancient introduce idea lead integral calculus develop idea rigorous way calculation volume area integral calculus th method mathematic method c

In [30]:
vectors = []
for article in articles_cleaned:
    inferred_vector = model.infer_vector([article])
    vectors.append(inferred_vector)

In [55]:
vectors

[array([ 2.31774285e-01,  6.57590091e-01,  9.96707827e-02,  9.28357765e-02,
         1.76810309e-01,  2.48912675e-03,  1.19814239e-02,  9.38236490e-02,
        -1.26318729e+00,  5.51768899e-01,  6.03392005e-01, -2.46726558e-01,
        -6.97417617e-01, -6.16100490e-01,  8.16793293e-02, -5.52868009e-01,
         3.68554033e-02,  2.81176299e-01,  1.52979493e-01,  7.94902071e-02,
        -4.01350521e-02,  2.96123415e-01, -4.08339292e-01, -3.39614242e-01,
         1.01703377e-02,  1.68011174e-01, -1.59398869e-01,  6.05744362e-01,
         3.37722987e-01, -8.22737720e-03, -3.39643359e-01, -1.35937393e-01,
        -1.99946538e-01, -1.38935432e-01,  2.19930839e-02,  2.36847952e-01,
        -1.60068929e-01,  2.70609647e-01,  3.04860413e-01, -2.97474414e-01,
         3.63241434e-02, -3.41268256e-02, -4.52622443e-01,  1.08214408e-01,
         7.11607933e-02,  2.12834701e-01,  1.11331508e-01, -6.14422746e-02,
        -2.85145338e-03, -1.98114827e-01,  8.87065083e-02, -3.04897636e-01,
         2.8

In [6]:
article_names = []
file = open(fileName + '_nodes.txt', "r")
for line in file:
    article_names.append(line.rstrip("\n"))
file.close()

df = pd.DataFrame(vectors)
df["article_name"] = article_names
#save to a file
df.to_hdf(fileName + "_embeddings_doc2vec.h5", key='df')


NameError: name 'vectors' is not defined

In [8]:
data_table = pd.read_hdf(fileName + "_embeddings_doc2vec.h5", 'df')

In [12]:
data_table.loc[data_table["article_name"] == "Equations_of_fluid_dynamics"]

0         1         2         3         4         5         6  \
57 -0.000767 -0.001426  0.000003  0.001473 -0.000209 -0.001602  0.001126   

          7         8         9  ...       291       292       293       294  \
57 -0.00008  0.001494  0.000747  ...  0.000785 -0.000311  0.001565  0.001588   

         295       296       297       298       299  \
57  0.000924  0.001572  0.001208  0.000725 -0.000862   

                   article_name  
57  Equations_of_fluid_dynamics  

[1 rows x 301 columns]